![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - S 2019 Pré-natal - Parte 2

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [2]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

[1] 293726   1087

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2019.1<-  <Coloque aqui o nome do arquivo RDATA>  %>% filter(V0025A==1) 
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(90846/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00562  0.26621  0.54401  1.00000  1.12765 61.09981 

## Criação de variáveis dos indicadores

In [4]:
#Desfechos - Indicadores
# 6. Proporção de mulheres que tiveram a pressão arterial medida em todas as consultas - S006P.
pns2019.1$S006P <- NA
pns2019.1$S006P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S006P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S07901==1] <- 1
pns2019.1$S006P<-factor(pns2019.1$S006P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S006P)

# 7. Proporção de mulheres que realizaram pré-natal e que tiveram o peso medido em todas as consultas - S007P.
pns2019.1$S007P <- NA
pns2019.1$S007P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S007P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S07902==1] <- 1
pns2019.1$S007P<-factor(pns2019.1$S007P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S007P)

# 8. Proporção de mulheres que tiveram a barriga medida em algumas/todas as consultas - S008P.
pns2019.1$S008P <- NA
pns2019.1$S008P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S008P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & (pns2019.1$S07903==1 | pns2019.1$S07903==2)] <- 1
pns2019.1$S008P<-factor(pns2019.1$S008P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S008P)

# 9. Proporção de mulheres que tiveram o coração do bebê ouvido em todas consultas - S009P.
pns2019.1$S009P <- NA
pns2019.1$S009P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S009P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & (pns2019.1$S07904==1)] <- 1
pns2019.1$S009P<-factor(pns2019.1$S009P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S009P)

# 10. Proporção de mulheres que tiveram exame das mamas em algumas/todas consultas - S010P.
pns2019.1$S010P <- NA
pns2019.1$S010P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 ] <- 2
pns2019.1$S010P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & (pns2019.1$S07905==1 | pns2019.1$S07905==2)] <- 1
pns2019.1$S010P<-factor(pns2019.1$S010P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S010P)

Sim   Não  NA's 
 2561   173 88112

Sim   Não  NA's 
 2585   149 88112

Sim   Não  NA's 
 2663    71 88112

Sim   Não  NA's 
 2208   526 88112

Sim   Não  NA's 
  833  1901 88112

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

urbano  rural 
 69873  20973

### UF

In [6]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Pará               Amapá           Tocantins            Maranhão 
               3853                1554                1922                5080 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               5209                3541                4966                6114 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goiás    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [7]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       17602        31544        19830        11472        10398

### Capital

In [8]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          2176           2380           3479           2238           3853 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3967           3738           3767           2863           2468 
       Goiânia       Brasília 
          2702           2365

### Faixa Etária

In [9]:
#Faixas Etárias

pns2019.1 <- pns2019.1 %>% mutate(fx_idade_S=cut(C008,
  breaks = c(18,25,30,40,120),
  labels = c("18 a 24 anos", "25 a 29 anos", "30 a 39 anos", "40 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$fx_idade_S)

18 a 24 anos    25 a 29 anos    30 a 39 anos 40 anos ou mais            NA's 
           8145            7249           18150           54987            2315

### Raça

In [10]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 33133  10345  45994   1374

### Renda per capita

In [11]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4, 
                        ifelse(is.na(VDF004)==TRUE, NA_real_, 5))))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       23697        26406        22466         7612        10643           22

### Escolaridade

In [12]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2019.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                36276                                 13520 
   Superior incompleto ou equivalente                     Superior completo 
                                27433                                 13617

## Criando indicadores

### Filtrando base de indicadores

In [13]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Ssurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "C008", "C006", "C009", "V0031", 
                                      "Sit_Urbano_Rural", "Unidades_da_Federacao", "GrandesRegioes",  "Capital", "fx_idade_S", "Raca", "rend_per_capita", "gescol",
                                      "S006P", "S007P", "S008P", "S009P", "S010P", "S068") 
summary(pns2019Ssurvey)

     V0024            UPA_PNS      peso_morador_selec      C008       
 1210010: 1167   140001681:   18   Min.   : 0.00562   Min.   : 15.00  
 1410011:  792   140003815:   18   1st Qu.: 0.26621   1st Qu.: 32.00  
 2710111:  779   140005777:   18   Median : 0.54401   Median : 45.00  
 2410011:  745   140006746:   18   Mean   : 1.00000   Mean   : 46.39  
 5010011:  738   140007081:   18   3rd Qu.: 1.12765   3rd Qu.: 60.00  
 3210011:  711   140007715:   18   Max.   :61.09981   Max.   :107.00  
 (Other):85914   (Other)  :90738                                      
      C006            C009           V0031       Sit_Urbano_Rural
 Min.   :1.000   Min.   :1.000   Min.   :1.000   urbano:69873    
 1st Qu.:1.000   1st Qu.:1.000   1st Qu.:1.000   rural :20973    
 Median :2.000   Median :4.000   Median :2.000                   
 Mean   :1.529   Mean   :2.679   Mean   :2.605                   
 3rd Qu.:2.000   3rd Qu.:4.000   3rd Qu.:4.000                   
 Max.   :2.000   Max.   :9.000   Max

### Exporta tabela filtrada com os dados específicos - Módulo S 2019 - Parte2 

In [14]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Ssurvey, file.path(diretorio_saida, "pns2019Ssurvey.csv"))

### Cria plano amostral complexo

In [15]:
desPNS=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, 
                 data=pns2019Ssurvey)

In [16]:
#survey design S006P a S010P
desPNSS006P=subset(desPNS, C006==2 & C008>=18 & S068==1)
desPNSS006P_C=subset(desPNS, C006==2 & C008>=18 & S068==1 & V0031==1)
desPNSS006P_R=subset(desPNS, C006==2 & C008>=18 & S068==1 & !is.na(Raca))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [17]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [18]:
ListaIndicadores = c(~S006P, ~S007P, ~S008P, ~S009P, ~S010P)
ListaIndicadoresTexto = c("S006P", "S007P", "S008P", "S009P", "S010P" )
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

In [19]:
ListaDominiosS001 = c(~Raca,~rend_per_capita,~fx_idade_S,~Sit_Urbano_Rural,
                      ~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTextoS001= c("raça","rend_per_capita","fx_idade_S","urb_rur",
                          "uf","região","capital","gescol") 

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [20]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1; j <- 1
    if (ListaIndicadoresTexto[i]== "S006P" | ListaIndicadoresTexto[i]== "S007P" | ListaIndicadoresTexto[i]== "S008P" | ListaIndicadoresTexto[i]== "S009P" | ListaIndicadoresTexto[i]== "S010P"){
        ListaDominios<-ListaDominiosS001
        ListaDominiosTexto<-ListaDominiosTextoS001
        } else {
                    ListaDominios<-ListaDominiosS001
ListaDominiosTexto<-ListaDominiosTextoS001
                }
    #Para cada dominio
    for (dominio in ListaDominios){
#design especifico para capital que é subconjunto do dataframe total
         if (ListaDominiosTexto[j]=="capital"){
#designs especificos por variavel que são subconjuntos do dataset total
            if (ListaIndicadoresTexto[i]== "S006P" |  ListaIndicadoresTexto[i]== "S007P" | ListaIndicadoresTexto[i]== "S008P"| ListaIndicadoresTexto[i]== "S009P"){
              dataframe_indicador<-svyby( indicador , dominio , desPNSS006P_C , svymean,vartype= c("ci","cv")) 
              } else if (ListaIndicadoresTexto[i]== "S010P") {
                    dataframe_indicador<-svyby( indicador , dominio , desPNSS006P_C, svymean,vartype= c("ci","cv"))
                        }
               } else if  (ListaDominiosTexto[j]=="raça"){
                    if (ListaIndicadoresTexto[i]== "S006P" | ListaIndicadoresTexto[i]== "S007P" |  ListaIndicadoresTexto[i]== "S008P" |  ListaIndicadoresTexto[i]== "S009P"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS006P_R , svymean,vartype= c("ci","cv"))
                        } else if
(ListaIndicadoresTexto[i]== "S010P"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS006P_R , svymean,vartype= c("ci","cv"))
                        }
               #design geral para o subconjunto maior que 15 anos
                 } else { 
                        if (ListaIndicadoresTexto[i]== "S006P" | ListaIndicadoresTexto[i]== "S007P" | ListaIndicadoresTexto[i]== "S008P" | ListaIndicadoresTexto[i]== "S009P"){
                                dataframe_indicador<-svyby( indicador , dominio , desPNSS006P , svymean,vartype= c("ci","cv"))
                            } else if
(ListaIndicadoresTexto[i]== "S010P")
                     {
                                dataframe_indicador<-svyby( indicador , dominio , desPNSS006P , svymean,vartype= c("ci","cv"))
                            }
                        }
#União do dataframe de indicadores no formato do painel disponibilizado para PNS
dataframe_indicador<-data.frame(dataframe_indicador)
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [21]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [22]:
i = 0
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i + 1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset total
                if (ListaIndicadoresTexto[i]== "S006P" | ListaIndicadoresTexto[i]== "S007P" | ListaIndicadoresTexto[i]== "S008P"| ListaIndicadoresTexto[i]== "S009P"){
                            dataframe_indicador <- svymean(indicador,desPNSS006P_C)
                        } else if
(ListaIndicadoresTexto[i]== "S010P"){
                            dataframe_indicador <- svymean(indicador,desPNSS006P_C)
                    }
                } else {
                if (ListaIndicadoresTexto[i]== "S006P" | ListaIndicadoresTexto[i]== "S007P" | ListaIndicadoresTexto[i]== "S008P"| ListaIndicadoresTexto[i]== "S009P"){
                            dataframe_indicador <- svymean(indicador,desPNSS006P)
                        } else if
(ListaIndicadoresTexto[i]== "S010P"){
                            dataframe_indicador <- svymean(indicador,desPNSS006P)
                    }
                }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
    }
}

In [23]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim       LowerS    UpperS   
S006PSim  total    Brasil   2019 S006P     0.9477060 0.9358079 0.9596041
S006PSim1 total    Capital  2019 S006P     0.9447823 0.9259869 0.9635778
S007PSim  total    Brasil   2019 S007P     0.9532179 0.9414090 0.9650268
S007PSim1 total    Capital  2019 S007P     0.9536965 0.9346891 0.9727039
S008PSim  total    Brasil   2019 S008P     0.9706513 0.9588280 0.9824745
S008PSim1 total    Capital  2019 S008P     0.9779854 0.9653568 0.9906139
S009PSim  total    Brasil   2019 S009P     0.8143380 0.7916183 0.8370577
S009PSim1 total    Capital  2019 S009P     0.8167267 0.7804770 0.8529764
S010PSim  total    Brasil   2019 S010P     0.3625718 0.3297028 0.3954409
S010PSim1 total    Capital  2019 S010P     0.4309147 0.3771172 0.4847121
          cvS        
S006PSim  0.006405528
S006PSim1 0.010150173
S007PSim  0.006320746
S007PSim1 0.010168667
S008PSim  0.006214775
S008PSim1 0.006588311
S009PSim  0.014234744
S009PSim1 0.022645383
S010PSim  0.046253562
S010PSim1 0.063697480

#### Unindo tabela de indicadores e de totais

In [24]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [25]:
matrizIndicadores

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_S     
25 a 29 anos                           fx_idade_S     
30 a 39 anos                           fx_idade_S     
40 anos ou mais                        fx_idade_S     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
João Pessoa4                           capital        
Recife4                                capital        
Maceió4                                capital        
Aracaju4                               capital        
Salvador4                              capital        
Belo Horizonte4                        capital        
Vitória4                               capital        
Rio de Janeiro9                        capital        
São Paulo8                             capital        
Curitiba4                              capital        
Florianópolis4                         capital        
Porto Alegre4                          capital        
Campo Grande4                          capital        
Cuiabá4                                capital        
Goiânia4                               capital        
Brasília4                              capital        
Fundamental incompleto ou equivalente4 gescol         
Médio incompleto ou equivalente4       gescol         
Superior incompleto ou equivalente4    gescol         
Superior completo4                     gescol         
S006PSim                               total          
S006PSim1                              total          
S007PSim                               total          
S007PSim1                              total          
S008PSim                               total          
S008PSim1                              total          
S009PSim                               total          
S009PSim1                              total          
S010PSim                               total          
S010PSim1                              total          
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

In [26]:
matrizIndicadores_cv= subset(matrizIndicadores, matrizIndicadores$cvS>0.30)
matrizIndicadores_cv

abr_tipo abr_nome    Ano  Indicador Sim        LowerS      
Rondônia4    uf       Rondônia    2019 S010P     0.14414580  0.045523932
Acre4        uf       Acre        2019 S010P     0.17103094  0.021710491
Roraima4     uf       Roraima     2019 S010P     0.14047197  0.034479287
Amapá4       uf       Amapá       2019 S010P     0.15446528  0.041395021
Tocantins4   uf       Tocantins   2019 S010P     0.20078192  0.075294990
Porto Velho4 capital  Porto Velho 2019 S010P     0.13378315  0.024767904
Rio Branco4  capital  Rio Branco  2019 S010P     0.10641712  0.001993107
Boa Vista4   capital  Boa Vista   2019 S010P     0.17462065  0.028415842
Belém4       capital  Belém       2019 S010P     0.27229725  0.054425379
Macapá4      capital  Macapá      2019 S010P     0.09110738 -0.009283284
Palmas4      capital  Palmas      2019 S010P     0.32739968  0.130858595
São Luís4    capital  São Luís    2019 S010P     0.28881737  0.099542378
Natal4       capital  Natal       2019 S010P     0.23060926  0.061300854
Recife4      capital  Recife      2019 S010P     0.35279425  0.095921585
Aracaju4     capital  Aracaju     2019 S010P     0.37569552  0.144202348
Salvador4    capital  Salvador    2019 S010P     0.26790560  0.068323987
Vitória4     capital  Vitória     2019 S010P     0.47595719  0.195301798
Cuiabá4      capital  Cuiabá      2019 S010P     0.36865000  0.137268593
Goiânia4     capital  Goiânia     2019 S010P     0.37006473  0.129432871
             UpperS    cvS      
Rondônia4    0.2427677 0.3490785
Acre4        0.3203514 0.4454475
Roraima4     0.2464646 0.3849800
Amapá4       0.2675355 0.3734818
Tocantins4   0.3262688 0.3188789
Porto Velho4 0.2427984 0.4157552
Rio Branco4  0.2108411 0.5006576
Boa Vista4   0.3208255 0.4271869
Belém4       0.4901691 0.4082346
Macapá4      0.1914980 0.5622011
Palmas4      0.5239408 0.3062859
São Luís4    0.4780924 0.3343658
Natal4       0.3999177 0.3745878
Recife4      0.6096669 0.3714910
Aracaju4     0.6071887 0.3143794
Salvador4    0.4674872 0.3800937
Vitória4     0.7566126 0.3008551
Cuiabá4      0.6000314 0.3202330
Goiânia4     0.6106966 0.3317625

#### Exportando tabela de indicadores calculados - Módulo S 2019

In [27]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2019S_R.csv"),sep = ";",dec = ",",row.names = FALSE)